In [3]:
from langchain_community.agent_toolkits import create_sql_agent
from langchain_openai import ChatOpenAI
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.pydantic_v1 import BaseModel, Field
import pandas as pd
from pydantic import BaseModel, Field

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


gpt = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
#agent_gpt_executor = create_sql_agent(gpt, db=db, agent_type="tool-calling", verbose=True)

## make database
from langchain_community.utilities import SQLDatabase
from sqlalchemy import create_engine

from langchain.prompts import ChatPromptTemplate
from langchain.schema import SystemMessage
from langchain_core.prompts import MessagesPlaceholder
#agent_groq_executor = create_sql_agent(llm, db=db, agent_type="tool-calling", verbose=True)

from OpenAITools.FetchTools import fetch_clinical_trials, fetch_clinical_trials_jp
from OpenAITools.CrinicalTrialTools import QuestionModifierEnglish, TumorNameExtractor, SimpleClinicalTrialAgent,GraderAgent,LLMTranslator,generate_ex_question_English

groq = ChatGroq(model_name="llama3-70b-8192", temperature=0)
#agent_groq_executor = create_sql_agent(groq, db=db, agent_type="tool-calling", verbose=True)

age = "65"
sex ="男性"
tumor_type ="胃癌"
#tumor_type = "gastric cancer"
GeneMutation ="HER2"
Meseable = "有り"
Biopsiable = "有り"
NCTID = 'NCT06441994'

#Define extractor
Translator = LLMTranslator(groq)
TumorName = Translator.translate(tumor_type)

#Make db
df = fetch_clinical_trials(TumorName)
# 新しい列を追加
df['AgentJudgment'] = None
df['AgentGrade'] = None
#df = df.iloc[:5, :]
NCTIDs = list(df['NCTID' ])

#Define agents
#modifier = QuestionModifierEnglish(groq)
CriteriaCheckAgent = SimpleClinicalTrialAgent(groq)
grader_agent = GraderAgent(groq)

Fetching data from: https://clinicaltrials.gov/api/v2/studies?query.titles=Stomach cancer SEARCH[Location](AREA[LocationCountry]Japan AND AREA[LocationStatus]Recruiting)&pageSize=100


In [4]:
ex_question = generate_ex_question_English(age, sex, TumorName, GeneMutation, Meseable, Biopsiable)

In [5]:
for nct_id in NCTIDs:
    TargetCriteria = df.loc[df['NCTID'] == nct_id, 'Eligibility Criteria'].values[0]
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)

    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    # NCTIDに一致する行を見つけて更新
    df.loc[df['NCTID'] == nct_id, 'AgentJudgment'] = AgentJudgment
    df.loc[df['NCTID'] == nct_id, 'AgentGrade'] = AgentGrade

The patient is not eligible for this clinical trial because the trial is for metastatic breast cancer (mBC) or metastatic gastric adenocarcinoma, gastroesophageal junction adenocarcinoma, or esophageal adenocarcinoma (mGEAC), and the patient has stomach cancer, which is not explicitly mentioned in the inclusion criteria.
no
The patient is eligible for this clinical trial based on the provided information, as they meet the inclusion criteria (age, measurable tumor, biopsiable tumor, and HER2 gene mutation) and do not have any of the exclusion criteria mentioned.
yes
The patient is eligible for this clinical trial based on the provided information, as he has a known HER2 gene mutation and a measurable and biopsiable tumor. However, I do not know if he meets the other inclusion criteria, such as adequate bone marrow, renal, and liver function, and performance status.
unclear
The 65-year-old male patient with Stomach cancer is eligible for this clinical trial based on the provided criteria

In [7]:
 # 列を指定した順に並び替え
columns_order = ['NCTID', 'AgentGrade', 'Title', 'AgentJudgment', 'Japanes Locations', 
                     'Primary Completion Date', 'Cancer', 'Summary', 'Eligibility Criteria']
df = df[columns_order]        

In [8]:
df

NCTID AgentGrade                                              Title  \
0   NCT06324357         no  Beamion BCGC-1: A Study to Find a Suitable Dos...   
1   NCT06490055        yes  Predicting the Efficacy in Advanced Gastric Ca...   
2   NCT05002127    unclear  A Study of Evorpacept (ALX148) in Patients wit...   
3   NCT04379596        yes  Ph1b/2 Study of the Safety and Efficacy of T-D...   
4   NCT05205343        yes  Trans-Pacific Multicenter Collaborative Study ...   
5   NCT05365581        yes  A Study of ASP2138 Given by Itself or Given Wi...   
6   NCT00197470    unclear    Cytokine Gene Polymorphisms in Gastric Diseases   
7   NCT06056024         no  A Study to Test How Well Different Doses of BI...   
8   NCT05438459         no  GAIA-102 Intraperitoneal Administration in Pat...   
9   NCT06490159        yes  Predicting Peripheral Neuropathy of Paclitaxel...   
10  NCT06038578         no  A Study of TRK-950 When Used in Combination Wi...   
11  NCT05152147        yes  A Study of Zanidatamab in Combination With Che...   
12  NCT05322577         no  A Study Evaluating Bemarituzumab in Combinatio...   

                                        AgentJudgment  \
0   The patient is not eligible for this clinical ...   
1   The patient is eligible for this clinical tria...   
2   The patient is eligible for this clinical tria...   
3   The 65-year-old male patient with Stomach canc...   
4   The patient is eligible for this clinical tria...   
5   The patient is eligible for this clinical tria...   
6   I do not know if the patient is eligible for t...   
7   The patient is not eligible for this clinical ...   
8   The patient is not eligible for this clinical ...   
9   The patient is eligible for this clinical tria...   
10  The patient is not eligible for this clinical ...   
11  The 65-year-old male patient with Stomach canc...   
12  The patient is not eligible for this clinical ...   

                                    Japanes Locations Primary Completion Date  \
0                                             ku, shi              2027-02-22   
1                                           Kurashiki              2025-12-31   
2   Chiba, Fukuoka, Gifu, Kumamoto, Kyoto, Nagasak...                 2026-07   
3                               Kashiwa, gun, ku, shi              2026-07-30   
4                                               Tokyo              2026-05-31   
5   Kashiwa, Nagoya, Osakasayama, Suita, Yokohama, ku              2026-10-31   
6                                           Hamamatsu            Unknown Date   
7                                         Kashiwa, ku              2027-05-26   
8                                                 shi              2026-12-31   
9                                           Kurashiki              2025-12-31   
10                               Chuo Ku, Kashiwa, Ku              2025-08-31   
11  Cho, Chuo Ku, Hirakata, Ina, Ku, Matsuyama, Na...              2024-12-31   
12                                  Shi, gun, ku, shi              2026-03-17   

                                               Cancer  \
0   Metastatic Breast Cancer, Metastatic Gastric A...   
1   Gastric Cancer, Chemotherapy Effect, Paclitaxe...   
2   Gastric Cancer, Gastroesophageal Junction Aden...   
3                                      Gastric Cancer   
4       Gastrostomy, Gastric, GastroEsophageal Cancer   
5   Gastric Adenocarcinoma, Gastroesophageal Junct...   
6       Gastric Ulcer, Duodenal Ulcer, Gastric Cancer   
7                          Solid Tumor, KRAS Mutation   
8                   Gastric Cancer, Pancreatic Cancer   
9   Gastric Cancer, Chemotherapy-induced Periphera...   
10  Gastric Adenocarcinoma, Gastric Cancer, Gastro...   
11  Gastric Neoplasms, Gastroesophageal Adenocarci...   
12   Gastric Cancer, Gastroesophageal Junction Cancer   

                                              Summary  \
0   This study is open to adults aged 18 years and...   
1   With advances in chemoth